In [639]:
import matplotlib.pyplot as plt
import numpy as np
import csv
import pandas as pd
import scanpy as sc
import sys
import scanpy as sc
import scipy.sparse
import seaborn as sns
from itertools import *
import ggplot

AttributeError: module 'pandas' has no attribute 'tslib'

In [63]:
def read_sc(count, meta, celltype_key='cell_type', batch_key=None, categorical_covariate_key=None,
            continuous_covariate_key=None):
    count = sc.read_csv(count)
    count.X = scipy.sparse.csc_matrix(count.X)

    meta = pd.read_csv(meta, index_col=0)

    if all(count.obs.index == meta.index):
        count.obs = pd.concat([count.obs, meta], axis=1)

    if celltype_key not in count.obs.columns:
        raise KeyError('celltype_key ' + celltype_key + ' not found in ' + ', '.join(count.obs.columns) + '!')
    if batch_key is not None and batch_key not in count.obs.columns:
        raise KeyError('batch_key ' + batch_key + ' not found in ' + ', '.join(count.obs.columns) + '!')
    if categorical_covariate_key is not None and not all(x in count.obs.columns for x in categorical_covariate_key):
        raise KeyError('categorical_covariate_key ' + categorical_covariate_key + 'is not a subset of ' + ', '.join(
            count.obs.columns) + '!')
    if continuous_covariate_key is not None and not all(x in count.obs.columns for x in continuous_covariate_key):
        raise KeyError('continuous_covariate_key ' + continuous_covariate_key + 'is not a subset of ' + ', '.join(
            count.obs.columns) + '!')

    return count

In [50]:
def process_to_cpdb(sc_path, save_path, name="test", annotation_name="cell_type"):
    adata_sc = sc.read_h5ad(sc_path)
    adata_sc.X = adata_sc.X.A

    utils.warn(' --- Generating count file --- ')
    # set df.dtypes = float32
    df_expr_matrix = pd.DataFrame(sc.pp.normalize_total(adata_sc, inplace=False)["X"], dtype="float")
    df_expr_matrix = df_expr_matrix.T
    # set cell ids as columns
    df_expr_matrix.columns = adata_sc.obs.index
    # genes should be either Ensembl IDs or gene names
    # transform orthologs
    index = adata_sc.var.index
    genes = got.rename_gene(np.array(index))
    df_expr_matrix.set_index(genes, inplace=True)

    utils.warn(' --- Saving count file... --- ')
    df_expr_matrix.to_csv(save_path + name + ".counts.txt", sep='\t')

    utils.warn(' --- Generating metadata file --- ')
    df_meta = pd.DataFrame(
        data={'Cell': list(adata_sc.obs.index), 'cell_type': list(adata_sc.obs[annotation_name])}
    )
    df_meta.set_index('Cell', inplace=True)
    utils.warn(' --- Saving metadata file... --- ')
    df_meta.to_csv(save_path + name + ".meta.txt", sep='\t')

In [51]:
if __name__ == "__main__":
    process_to_cpdb(
        sc_path="../data/STW-M-Brain-Stereo-seq-1/coronal_1.bin50.adata_sc.clusters.h5ad",
        annotation_name="cell_type",
        save_path="../data/STW-M-Brain-Stereo-seq-1/",
        name="coronal_1"
    )

In [454]:
def interaction_heatmap(means_path, pvalues_path, output_path="data/STW-M-Brain-Stereo-seq-1/out/", output_name="heatmap"):
    means = pd.read_csv(means_path, sep='\t')
    pvalues = pd.read_csv(pvalues_path, sep='\t')
    means.index = means["interacting_pair"]
    pvalues.index = pvalues["interacting_pair"]
    means_filter = pd.DataFrame()
    pvalues_filter = pd.DataFrame()
    # select any pairs meet pavlue <= 0.01
    for i in range(0,len(pvalues)):
         if any(pvalues.iloc[i,12:] <= 0.01):
            pvalues_filter = pvalues_filter.append(pvalues.iloc[i])
            means_filter = means_filter.append(means.iloc[i])
    means_filter = np.log2(means_filter.iloc[:,:75].T)
    means_filter = means_filter.replace(-np.inf, -2)
    pvalues_filter = -np.log10(pvalues_filter.iloc[:,:75].T)
    pvalues_filter = pvalues_filter.replace(np.inf, 6)
    pvalues_filter = pvalues_filter.where(pvalues_filter<6,6)
    hplot = sns.clustermap(
        pvalues_filter,
        cmap="OrRd",
        cbar_pos=[.8, .9, .01, .08],
        cbar_kws={'ticks':(0,2,4,6)},
        dendrogram_ratio=(0,.1),
        figsize=(16,9)
    )
    hplot.ax_heatmap.yaxis.set_ticks_position("left")
    hplot.ax_row_dendrogram.set_visible(False)
    #hplot.ax_row_dendrogram.set_ticks_position("right")
    hplot.ax_heatmap.set_xticklabels(hplot.ax_heatmap.get_xticklabels(), fontsize=6, rotation=45, horizontalalignment="right")
    hplot.ax_heatmap.set_yticklabels(hplot.ax_heatmap.get_yticklabels(), fontsize=6)
    hplot.savefig(output_path+output_name+'.pdf')
    

In [693]:
def select_cell_pairs_from_microenv(microenvs):
    microenvs = pd.read_csv(microenvs, sep=',')
    microenvs_cell_pairs = pd.Series(index=np.unique(microenvs["microenvironment"]))
    for env in microenvs_cell_pairs.index:
        cell_types = microenvs.loc[microenvs["microenvironment"]==env]["cell_type"]
        for i in cell_types:
            for j in cell_types:
                cell_type = i+'|'+j
                microenvs_cell_pairs[env] = np.append(microenvs_cell_pairs[env], cell_type)
    for env in microenvs_cell_pairs.index:
        microenvs_cell_pairs[env] = microenvs_cell_pairs[env][1:]
    return microenvs_cell_pairs

In [744]:
def interaction_dotplot(means_path, pvalues_path, output_path="data/STW-M-Brain-Stereo-seq-1/out/", output_name="dot_plot", microenvs_cell_pairs=None):
    means = pd.read_csv(means_path, sep='\t')
    pvalues = pd.read_csv(pvalues_path, sep='\t')
    pvalues_all = pd.melt(pvalues, id_vars=['interacting_pair'], value_vars=pvalues.columns[11:], var_name="cell_pairs", value_name="pvalue")
    pvalues_all["pvalue"] = -np.log10(pvalues_all["pvalue"])
    pvalues_all["pvalue"] = pvalues_all["pvalue"].replace(np.inf, 6)
    means_all = pd.melt(means, id_vars=['interacting_pair'], value_vars=means.columns[11:], var_name="cell_pairs", value_name="mean_expr")
    means_all["mean_expr"] = -np.log2(means_all["mean_expr"])
    means_all["mean_expr"] = means_all["mean_expr"].replace(-np.inf, -6)
    
    # filter out pvalue > 0.01
    pvalues_all = pvalues_all.where(pvalues_all["pvalue"]>= 2).dropna(axis=0)
    # merge pvalues and means
    pvalues_means_all = pvalues_all.merge(means_all, how="left", on=["interacting_pair","cell_pairs"])
    height = np.log2(len(np.unique(pvalues_means_all["cell_pairs"])))*6
    aspect = len(np.unique(pvalues_means_all["interacting_pair"]))/(height*height)
    
    g = sns.relplot(
        data=pvalues_means_all,
        x="interacting_pair",y="cell_pairs",
        hue="mean_expr",size="pvalue",
        palette="magma", height=height, aspect=1,
        legend="full"
    )

    # Tweak the figure to finalize
    g.ax.set_xticklabels(g.ax.get_xticklabels(), fontsize=5, rotation=45, horizontalalignment="right")
    g.ax.set_yticklabels(g.ax.get_yticklabels(), fontsize=5)
    g.set(xlabel="", ylabel="", aspect="equal")
    g.despine(left=True, bottom=True)
    g.ax.margins(.02)
    legend = g.ax.legend()  
    legend.texts[0].set_text("$-log_2$ mean expr\n (molecule 1,molecule 2)")
    legend.texts[6].set_text("$-log_{10}$ p-value")
    g.savefig(output_path+output_name+'.pdf')
    plt.show()
    
    # for each microenvironment
    if microenvs_cell_pairs is not None:
        for env in microenvs_cell_pairs.index:
            pvalues_means_env = pvalues_means_all[pvalues_means_all["cell_pairs"].isin(microenvs_cell_pairs[env])]
            height = np.log2(len(microenvs_cell_pairs[env]))*6
            aspect = len(np.unique(pvalues_means_all["interacting_pair"]))/(height*height)
            g = sns.relplot(
                data=pvalues_means_env,
                x="interacting_pair",y="cell_pairs",
                hue="mean_expr",size="pvalue",
                palette="magma", height=height, aspect=1
            )

            # Tweak the figure to finalize
            g.ax.set_xticklabels(g.ax.get_xticklabels(), rotation=45, horizontalalignment="right")
            g.ax.set_yticklabels(g.ax.get_yticklabels())
            g.set(xlabel="", ylabel="", aspect="equal")
            g.despine(left=True, bottom=True)
            g.ax.margins(.08)
            g.tight_layout()
            g.savefig(output_path + output_name+ '.' + env+'.pdf')
            plt.show()

In [745]:
microenvs_cell_pairs = select_cell_pairs_from_microenv(microenvs = "data/STW-M-Brain-Stereo-seq-1/out/microenvironment.csv")
interaction_dotplot(means_path="data/STW-M-Brain-Stereo-seq-1/out/means.txt",
                    pvalues_path="data/STW-M-Brain-Stereo-seq-1/out/pvalues.txt",
                    #microenvs_cell_pairs=microenvs_cell_pairs
                   )

/tmp/ipykernel_214870/3212383522.py:3: DeprecationWarning: The default dtype for empty Series will be 'object' instead of 'float64' in a future version. Specify a dtype explicitly to silence this warning.
  microenvs_cell_pairs = pd.Series(index=np.unique(microenvs["microenvironment"]))
/home/user/BGM/rbase/env/anaconda3/envs/st_ann_anls/lib/python3.9/site-packages/pandas/core/series.py:726: RuntimeWarning: divide by zero encountered in log10
  result = getattr(ufunc, method)(*inputs, **kwargs)
/home/user/BGM/rbase/env/anaconda3/envs/st_ann_anls/lib/python3.9/site-packages/pandas/core/series.py:726: RuntimeWarning: divide by zero encountered in log2
  result = getattr(ufunc, method)(*inputs, **kwargs)
/tmp/ipykernel_214870/1701537259.py:27: UserWarning: FixedFormatter should only be used together with FixedLocator
  g.ax.set_xticklabels(g.ax.get_xticklabels(), fontsize=5, rotation=45, horizontalalignment="right")
/tmp/ipykernel_214870/1701537259.py:28: UserWarning: FixedFormatter shoul